In [1]:
import numpy as np
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib.animation import FFMpegWriter
%matplotlib qt

In [2]:
metadata = dict(title='Tess Orbit', artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

In [3]:
mE = 5.97*(10**24) #Earth
mM = 7.35*(10**22) #Moon
mT = 362 #TESS
G = 6.67*(10**-11) #gravitational cst
R = 384*(10**6) #Earth-Moon distance, mag(rE-rM)=R, rM=rE-R

xE = 0

xM = 384*(10**6)

xT = 375*(10**6)

rCM = np.array([((xM*mM)+(xE*mE))/(mM+mE),0,0])
rE = np.array([xE,0,0]-rCM)
rM = np.array([xM,0,0]-rCM)

rT = np.array([xT*0.79,0,xT*0.6]) #x=xT*cos(37 degrees),z=xT*sin(37 degrees)

print('rCM = '+str(rCM))
print('Shifted Earth Position: rE = '+str(rE))
print('Shifted Moon Position: rM = '+str(rM))
print('Tess Position: rT = '+str(rT))

rCM = [4670141.47431124       0.               0.        ]
Shifted Earth Position: rE = [-4670141.47431124        0.                0.        ]
Shifted Moon Position: rM = [3.79329859e+08 0.00000000e+00 0.00000000e+00]
Tess Position: rT = [2.9625e+08 0.0000e+00 2.2500e+08]


In [4]:
fig_orig = plt.figure()
ax_orig = plt.axes(projection='3d')
# ax_orig.scatter3D(0,0,0)
ax_orig.scatter3D(rCM[0],rCM[1],rCM[2],label='COM')
ax_orig.scatter3D(rE[0],rE[1],rE[2],label='Earth')
ax_orig.scatter3D(rM[0],rM[1],rM[2],label='Moon')
ax_orig.scatter3D(rT[0],rT[1],rT[2],label='Tess')
plt.legend()
plt.show()

In [5]:
mu = mE*mM/(mE+mM)
w = ((G*mE*mM)/((R**3)*mu))**0.5 #Moon's angular velocity

#v=wr

vE = np.array([0,w*np.linalg.norm(rE),0])
vM = np.array([0,w*np.linalg.norm(rM),0])
vT = np.array([0,w*np.linalg.norm(rT),0])

print('vE = ' + str(vE))
print('vM = ' + str(vM))
print('vT = ' + str(vT))

vE = [ 0.         12.46064091  0.        ]
vM = [   0.         1012.10920023    0.        ]
vT = [  0.        992.5701887   0.       ]


In [6]:
y = np.concatenate((rE,rM,rT,vE,vM,vT))
print('y = ' + str(y))

y = [-4.67014147e+06  0.00000000e+00  0.00000000e+00  3.79329859e+08
  0.00000000e+00  0.00000000e+00  2.96250000e+08  0.00000000e+00
  2.25000000e+08  0.00000000e+00  1.24606409e+01  0.00000000e+00
  0.00000000e+00  1.01210920e+03  0.00000000e+00  0.00000000e+00
  9.92570189e+02  0.00000000e+00]


In [7]:
def KeplerODE(t,y):
    global mE,mM,mT,G
    
    rE = y[0:3]
    rM = y[3:6]
    rT = y[6:9]
    vE = y[9:12]
    vM = y[12:15]
    vT = y[15:18]
    
    drEdt = vE
    drMdt = vM
    drTdt = vT
    
    FE = -mE*mM*G*(rE-rM)/np.linalg.norm(rE-rM)**3 + -mE*mT*G*(rE-rT)/np.linalg.norm(rE-rT)**3
    FM = -mM*mE*G*(rM-rE)/np.linalg.norm(rM-rE)**3 + -mM*mT*G*(rM-rT)/np.linalg.norm(rM-rT)**3
    FT = -mT*mE*G*(rT-rE)/np.linalg.norm(rT-rE)**3 + -mT*mM*G*(rT-rM)/np.linalg.norm(rT-rM)**3
    aE = FE/mE
    aM = FM/mM
    aT = FT/mT
    dvEdt = aE
    dvMdt = aM
    dvTdt = aT
    
    return np.concatenate((drEdt,drMdt,drTdt,dvEdt,dvMdt,dvTdt))

In [8]:
aM = 38474.8*(10**4) #semimajor axis Moon
aT = 2.4*(10**8) #semimajor axis Tess
PM = ((4*(np.pi**2)*(aM**3))/(G*(mM+mE)))**0.5 #period of Moon [s]
PT = ((4*(np.pi**2)*(aT**3))/(G*(mT+mE)))**0.5 #period of Tess [s]
print('Period of Moon: ' + str(PM/86400) + ' days')
print('Period of Tess: ' + str(PT/86400) + ' days')
dt = PM/1000
t = 0
tMax = PM

xEt = []
yEt = []
zEt = []
xMt = []
yMt = []
zMt = []
xTt = []
yTt = []
zTt = []
tt = []

y = np.concatenate((rE,rM,rT,vE,vM,vT))

fig = plt.figure(dpi=200)
with writer.saving(fig, "fpMoon3.mp4", dpi=200):
    while (t<tMax):
        rE = y[0:3]
        rM = y[3:6]
        rT = y[6:9]

        xEt.append(rE[0])
        yEt.append(rE[1])
        zEt.append(rE[2])
        xMt.append(rM[0])
        yMt.append(rM[1])
        zMt.append(rM[2])
        xTt.append(rT[0])
        yTt.append(rT[1])
        zTt.append(rT[2])
        tt.append(t)  

        f1 = KeplerODE(t,y)
        f2 = KeplerODE(t+dt/2.0,y+f1*dt/2.0)
        f3 = KeplerODE(t+dt/2.0,y+f2*dt/2.0)
        f4 = KeplerODE(t+dt,y+f3*dt)

        ax = plt.axes(projection='3d')
        ax.scatter3D(xEt,yEt,zEt,label='Earth' if t == 0 else "")
        ax.scatter3D(xMt,yMt,zMt,label='Moon' if t == 0 else "")
        ax.scatter3D(xTt,yTt,zTt,label='Tess' if t == 0 else "")
        ax.text(rM[0],rM[1],rM[2],s = 't: ' + str(np.round(t/86400,3)) + ' days')
        plt.xlim(-4*(10**8),4*(10**8))
        plt.ylim(-4*(10**8),4*(10**8))
        ax.set_zlim(-2*(10**8),2*(10**8))
        ax.legend()
        
        y = y + (f1 + 2.0*f2 + 2.0*f3 + f4) / 6.0 * dt
        t = t + dt
        writer.grab_frame()

Period of Moon: 27.33527844721322 days
Period of Tess: 13.549800655540718 days


No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles wi

No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles wi

No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles wi

No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles wi

No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles wi

No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles with labels found to put in legend.
No handles wi